Create Catalog & Schemas (Unity Catalog)

In [0]:
%sql
CREATE CATALOG IF NOT EXISTS social_media_catalog;

USE CATALOG social_media_catalog;

CREATE SCHEMA IF NOT EXISTS bronze;
CREATE SCHEMA IF NOT EXISTS silver;
CREATE SCHEMA IF NOT EXISTS gold;

In [0]:
%sql
USE CATALOG social_media_catalog;
USE SCHEMA bronze;

CREATE VOLUME IF NOT EXISTS raw_data;

Bronze Layer (Raw Ingestion)


In [0]:
from pyspark.sql.functions import current_timestamp, input_file_name, col

# Use a complete Unity Catalog volume path because unity catalog disables dbfs access
# Example: '/Volumes/social_media_catalog/bronze/social_media_raw/'
data_source_path = '/Volumes/social_media_catalog/bronze/social_media/Social Media Engagement Dataset.csv'

df_bronze = (
    spark.read
    .option("header", "true")
    .option("inferSchema", "true")
    .csv(data_source_path)
    .withColumn("ingestion_timestamp", current_timestamp())
    .withColumn("source_file", col("_metadata.file_path"))
)

df_bronze.write.format("delta") \
    .mode("append") \
    .saveAsTable("social_media_catalog.bronze.raw_data")


In [0]:
%sql
select * from social_media_catalog.bronze.raw_data

post_id timestamp day_of_week platform user_id location language text_content hashtags mentions keywords topic_category sentiment_score sentiment_label emotion_type toxicity_score likes_count shares_count comments_count impressions engagement_rate brand_name product_name campaign_name campaign_phase user_past_sentiment_avg user_engagement_growth buzz_change_rate ingestion_timestamp source_file kcqbs6hxybia 2024-12-09T11:26:15.000Z Monday Instagram user_52nwb0a6 Melbourne, Australia pt Just tried the Chromebook from Google. Best purchase ever. #Food Really interested in hearing your thoughts! #Food null price, unique, traditional, efficient Pricing 0.9826 Positive Confused 0.0376 1264 1704 701 18991 0.19319 Google Chromebook BlackFriday Launch 0.0953 -0.3672 19.1 2026-02-01T05:33:35.368Z dbfs:/Volumes/social_media_catalog/bronze/social_media/Social%20Media%20Engagement%20Dataset.csv vkmervg4ioos 2024-07-28T19:59:26.000Z Sunday Twitter user_ucryct98 Tokyo, Japan ru Just saw an ad for Microsoft Surface Laptop during the SpringBlast2025. Not worth the money. #MustHave, #Food #MustHave, #Food @CustomerService, @BrandCEO delivery, slow Delivery -0.3793 Negative Angry 0.9715 522 1803 359 52764 0.05086 Microsoft Surface Laptop PowerRelease Post-Launch 0.1369 -0.451 -42.6 2026-02-01T05:33:35.368Z dbfs:/Volumes/social_media_catalog/bronze/social_media/Social%20Media%20Engagement%20Dataset.csv memhx4o1x6yu 2024-11-23T14:00:12.000Z Saturday Reddit user_7rrev126 Beijing, China ru What's your opinion about Nike's Epic React? #Promo, #Food, #Trending Really interested in hearing your thoughts! #Promo, #Food, #Trending null reliable, budget, durable, experience Product -0.3596 Negative Confused 0.5124 2689 705 643 8887 0.45425 Nike Epic React BlackFriday Post-Launch 0.2855 -0.4112 17.4 2026-02-01T05:33:35.368Z dbfs:/Volumes/social_media_catalog/bronze/social_media/Social%20Media%20Engagement%20Dataset.csv bhyo6piijqt9 2024-09-16T04:35:25.000Z Monday YouTube user_4mxuq0ax Lagos, Nigeria en Bummed out with my new Diet Pepsi from Pepsi! Disappointed with the quality. #Reviews, #Sustainable #Reviews, #Sustainable @StyleGuide, @BrandSupport improved, competitive, luxury, fast Delivery -0.7282 Negative Sad 0.4002 1827 262 743 6696 0.42293 Pepsi Diet Pepsi LaunchWave Launch -0.2094 -0.0167 -5.5 2026-02-01T05:33:35.368Z dbfs:/Volumes/social_media_catalog/bronze/social_media/Social%20Media%20Engagement%20Dataset.csv c9dkiomowakt 2024-09-05T21:03:01.000Z Thursday Twitter user_l1vpox2k Berlin, Germany hi Just tried the Corolla from Toyota. Absolutely loving it. #Health, #Travel Really interested in hearing your thoughts! #Health, #Travel @BrandSupport, @InfluencerName innovation, budget, helpful, luxury Product 0.546 Positive Happy 0.0862 2005 1443 703 47315 0.08773 Toyota Corolla LocalTouchpoints Launch 0.6867 0.0807 38.8 2026-02-01T05:33:35.368Z dbfs:/Volumes/social_media_catalog/bronze/social_media/Social%20Media%20Engagement%20Dataset.csv e8rzr949rzkr 2024-07-28T03:21:09.000Z Sunday Reddit user_jzvf44eq Seoul, South Korea pt Nike PowerRelease is subpar! Can't wait to see what's coming next. #Discount Curious about your experience too. #Discount null fast, outdated, luxury, disappointing Pricing -0.5007 Negative Excited 0.7113 3828 751 441 7734 0.64908 Nike React CyberMonday Pre-Launch 0.9095 -0.4563 16.0 2026-02-01T05:33:35.368Z dbfs:/Volumes/social_media_catalog/bronze/social_media/Social%20Media%20Engagement%20Dataset.csv 32qywmjy84gk 2024-08-21T17:02:47.000Z Wednesday Instagram user_hpr07vl1 Madrid, Spain ja Not sure why with my new Pepsi Wild Cherry from Pepsi! Not worth the money. #Quality, #Promo, #Limited #Quality, #Promo, #Limited null improved, unique, premium, durable Support -0.5339 Negative Confused 0.4716 2814 173 974 24542 0.16139 Pepsi Pepsi Wild Cherry GlobalCampaign Launch -0.9263 -0.081 -13.4 2026-02-01T05:33:35.368Z dbfs:/Volumes/social_media_catalog/bronze/social_media/Social%20Media%20Engagement%20Dataset.csv wu063ci6mizp 2025-0

#Silver Layer (Cleaning + Business Logic)
Engagement Rate Formula = (likes + comments + shares) / impressions

In [0]:
from pyspark.sql.functions import col, upper, to_date, hour

df_silver = (
    spark.table("social_media_catalog.bronze.raw_data")
    .filter(col("impressions") > 0)
    .withColumn("platform", upper(col("platform")))
    .withColumn(
        "engagement_rate",
        (col("likes_count") + col("comments_count") + col("shares_count")) / col("impressions")
    )
)
df_silver = df_silver \
    .withColumn("timestamp_date", to_date("timestamp")) \
    .withColumn("timestamp_hour", hour("timestamp"))

df_silver.write.format("delta") \
    .mode("overwrite") \
    .option("mergeSchema", "true") \
    .saveAsTable("social_media_catalog.silver.social_media_clean")

# Delta Optimization
Delta OPTIMIZE reduces small-file overhead by compacting data, and ZORDER improves query performance through data skipping on frequently filtered columns like platform and date.

In [0]:
%sql
OPTIMIZE social_media_catalog.silver.social_media_clean
ZORDER BY (platform, timestamp);

path metrics List(0, 0, List(null, null, 0.0, 0, 0), List(null, null, 0.0, 0, 0), 0, List(minCubeSize(107374182400), List(0, 0), List(1, 2503150), 0, List(0, 0), 0, null), null, 0, 0, 1, 1, false, 0, 0, 1769926379019, 1769926379470, 8, 0, null, List(0, 0), null, 32, 32, 0, 0, null)

#Gold Layer (Analytics & Aggregates)
Gold Table 1: Platform Performance \
Gold Table 2: Content Type Performance \
Gold Table 3: Time-Series Trend

In [0]:
%sql
-- Table 1
CREATE OR REPLACE TABLE social_media_catalog.gold.platform_performance AS
SELECT
  platform,
  COUNT(post_id) AS total_posts,
  AVG(engagement_rate) AS avg_engagement_rate,
  SUM(impressions) AS total_impressions
FROM social_media_catalog.silver.social_media_clean
GROUP BY platform;

num_affected_rows num_inserted_rows

In [0]:
%sql
-- Table 2
CREATE OR REPLACE TABLE social_media_catalog.gold.content_type_performance AS
SELECT
  platform,
  AVG(engagement_rate) AS avg_engagement_rate,
  COUNT(*) AS total_posts
FROM social_media_catalog.silver.social_media_clean
GROUP BY platform;

num_affected_rows num_inserted_rows

In [0]:
%sql
-- Table 3
CREATE OR REPLACE TABLE social_media_catalog.gold.daily_engagement AS
SELECT
  timestamp_date,
  AVG(engagement_rate) AS avg_engagement
FROM social_media_catalog.silver.social_media_clean
GROUP BY timestamp_date
ORDER BY timestamp_date;

num_affected_rows num_inserted_rows

#Orchestration – Databricks Jobs 
Automate pipeline\ 



In [0]:
print(f"Bronze records loaded: {df_bronze.count()}")
print(f"Ingestion time: {current_timestamp()}")

Bronze records loaded: 12000
Ingestion time: Column<'current_timestamp()'>


In [0]:
%sql
-- List all tables
SHOW TABLES IN social_media_catalog.bronze;
SHOW TABLES IN social_media_catalog.silver;
SHOW TABLES IN social_media_catalog.gold;

-- Preview table
SELECT * FROM social_media_catalog.silver.social_media_clean LIMIT 10;

post_id timestamp day_of_week platform user_id location language text_content hashtags mentions keywords topic_category sentiment_score sentiment_label emotion_type toxicity_score likes_count shares_count comments_count impressions engagement_rate brand_name product_name campaign_name campaign_phase user_past_sentiment_avg user_engagement_growth buzz_change_rate ingestion_timestamp source_file timestamp_date timestamp_hour kcqbs6hxybia 2024-12-09T11:26:15.000Z Monday INSTAGRAM user_52nwb0a6 Melbourne, Australia pt Just tried the Chromebook from Google. Best purchase ever. #Food Really interested in hearing your thoughts! #Food null price, unique, traditional, efficient Pricing 0.9826 Positive Confused 0.0376 1264 1704 701 18991 0.19319677742088356 Google Chromebook BlackFriday Launch 0.0953 -0.3672 19.1 2026-02-01T02:04:04.881Z dbfs:/Volumes/social_media_catalog/bronze/social_media/Social%20Media%20Engagement%20Dataset.csv 2024-12-09 11 vkmervg4ioos 2024-07-28T19:59:26.000Z Sunday TWITTER user_ucryct98 Tokyo, Japan ru Just saw an ad for Microsoft Surface Laptop during the SpringBlast2025. Not worth the money. #MustHave, #Food #MustHave, #Food @CustomerService, @BrandCEO delivery, slow Delivery -0.3793 Negative Angry 0.9715 522 1803 359 52764 0.050868016071563944 Microsoft Surface Laptop PowerRelease Post-Launch 0.1369 -0.451 -42.6 2026-02-01T02:04:04.881Z dbfs:/Volumes/social_media_catalog/bronze/social_media/Social%20Media%20Engagement%20Dataset.csv 2024-07-28 19 memhx4o1x6yu 2024-11-23T14:00:12.000Z Saturday REDDIT user_7rrev126 Beijing, China ru What's your opinion about Nike's Epic React? #Promo, #Food, #Trending Really interested in hearing your thoughts! #Promo, #Food, #Trending null reliable, budget, durable, experience Product -0.3596 Negative Confused 0.5124 2689 705 643 8887 0.45425903004388435 Nike Epic React BlackFriday Post-Launch 0.2855 -0.4112 17.4 2026-02-01T02:04:04.881Z dbfs:/Volumes/social_media_catalog/bronze/social_media/Social%20Media%20Engagement%20Dataset.csv 2024-11-23 14 bhyo6piijqt9 2024-09-16T04:35:25.000Z Monday YOUTUBE user_4mxuq0ax Lagos, Nigeria en Bummed out with my new Diet Pepsi from Pepsi! Disappointed with the quality. #Reviews, #Sustainable #Reviews, #Sustainable @StyleGuide, @BrandSupport improved, competitive, luxury, fast Delivery -0.7282 Negative Sad 0.4002 1827 262 743 6696 0.4229390681003584 Pepsi Diet Pepsi LaunchWave Launch -0.2094 -0.0167 -5.5 2026-02-01T02:04:04.881Z dbfs:/Volumes/social_media_catalog/bronze/social_media/Social%20Media%20Engagement%20Dataset.csv 2024-09-16 4 c9dkiomowakt 2024-09-05T21:03:01.000Z Thursday TWITTER user_l1vpox2k Berlin, Germany hi Just tried the Corolla from Toyota. Absolutely loving it. #Health, #Travel Really interested in hearing your thoughts! #Health, #Travel @BrandSupport, @InfluencerName innovation, budget, helpful, luxury Product 0.546 Positive Happy 0.0862 2005 1443 703 47315 0.08773116347881221 Toyota Corolla LocalTouchpoints Launch 0.6867 0.0807 38.8 2026-02-01T02:04:04.881Z dbfs:/Volumes/social_media_catalog/bronze/social_media/Social%20Media%20Engagement%20Dataset.csv 2024-09-05 21 e8rzr949rzkr 2024-07-28T03:21:09.000Z Sunday REDDIT user_jzvf44eq Seoul, South Korea pt Nike PowerRelease is subpar! Can't wait to see what's coming next. #Discount Curious about your experience too. #Discount null fast, outdated, luxury, disappointing Pricing -0.5007 Negative Excited 0.7113 3828 751 441 7734 0.6490819756917507 Nike React CyberMonday Pre-Launch 0.9095 -0.4563 16.0 2026-02-01T02:04:04.881Z dbfs:/Volumes/social_media_catalog/bronze/social_media/Social%20Media%20Engagement%20Dataset.csv 2024-07-28 3 32qywmjy84gk 2024-08-21T17:02:47.000Z Wednesday INSTAGRAM user_hpr07vl1 Madrid, Spain ja Not sure why with my new Pepsi Wild Cherry from Pepsi! Not worth the money. #Quality, #Promo, #Limited #Quality, #Promo, #Limited null improved, unique, premium, durable Support -0.5339 Negative Confused 0.4716 2814 173 974 24542 0.16139678917773612 Pepsi Pepsi W

# STEP 5: Governance – Unity Catalog
Permissions

In [0]:
%sql
-- List all users and groups
SHOW GRANTS ON CATALOG social_media_catalog;

Principal ActionType ObjectType ObjectKey

For this demo project, Unity Catalog permissions are simplified:\
 all table access is granted to the project user only. No additional roles or users were created
since this is a portfolio/demo setup.\
GRANT SELECT ON SCHEMA social_media_catalog.gold TO `demo_user`;

#STEP 6: Analytics & Dashboard

In [0]:
%sql
SELECT * FROM social_media_catalog.gold.platform_performance
ORDER BY avg_engagement_rate DESC;

platform total_posts avg_engagement_rate total_impressions INSTAGRAM 16485 0.28713600147446994 823649897 FACEBOOK 17017 0.28641655224445306 847192500 YOUTUBE 17052 0.27919026119842505 860918933 REDDIT 16604 0.27873209262167675 815421831 TWITTER 16842 0.2593357292716125 836969273

#STEP 7: ML Component (MLflow)
ML Use Case

Predict engagement rate

In [0]:
import mlflow
import mlflow.sklearn
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split

df = spark.table("social_media_catalog.silver.social_media_clean").toPandas()

X = df[["impressions"]]
y = df["engagement_rate"]

X_train, X_test, y_train, y_test = train_test_split(X, y)

model = LinearRegression()
model.fit(X_train, y_train)

with mlflow.start_run():
    mlflow.log_param("model", "LinearRegression")
    mlflow.sklearn.log_model(model, "engagement_model")


2026/02/01 06:13:24 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.
